# TextCNN
1. 预训练词向量
2. TextCNN网络

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [2]:
! /opt/bin/nvidia-smi

Thu Jun 24 02:00:52 2021       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 460.32.03    Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla T4            Off  | 00000000:00:04.0 Off |                    0 |
| N/A   46C    P8    10W /  70W |      0MiB / 15109MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

# Content Preprocessing

In [3]:
import bz2
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import jieba
from tqdm import tqdm

## word vector

从词向量预训练模型中建立词到向量映射

In [4]:
with bz2.open('/content/drive/MyDrive/Colab Notebooks Project/NLP/TouTiao_text/sgns.weibo.word.bz2') as f:
    info, *content = [x.decode('utf-8') for x in f.readlines()]

In [5]:
word_to_vector = {}

for ls in tqdm(content):
    word, *vector = ls.split()
    word_to_vector[word] = np.array(vector).astype(np.float64)

vector_dim = int(info.split()[1])
word_to_vector['UNK'] = np.random.random(size=vector_dim)
word_to_vector['PAD'] = np.zeros(shape=vector_dim)

100%|██████████| 195202/195202 [00:38<00:00, 5128.40it/s]


## training data

1. 对训练数据的词转化成对应的id，如果预训练没有的词则统一变成‘UNK’标识 
2. 对文本数据进行初步清洗

In [6]:
df_data = pd.read_csv('/content/drive/MyDrive/Colab Notebooks Project/NLP/TouTiao_text/train.csv')
df_data['sentence_cut'] = df_data['sentence'].apply(jieba.lcut)
df_data['label_for_train'] = pd.factorize(df_data['label'])[0]
df_data.info()

Building prefix dict from the default dictionary ...
Dumping model to file cache /tmp/jieba.cache
Loading model cost 0.940 seconds.
Prefix dict has been built successfully.


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 53360 entries, 0 to 53359
Data columns (total 6 columns):
 #   Column           Non-Null Count  Dtype 
---  ------           --------------  ----- 
 0   id               53360 non-null  int64 
 1   label            53360 non-null  int64 
 2   label_desc       53360 non-null  object
 3   sentence         53360 non-null  object
 4   sentence_cut     53360 non-null  object
 5   label_for_train  53360 non-null  int64 
dtypes: int64(3), object(3)
memory usage: 2.4+ MB


In [7]:
word_to_id = {'UNK': 0, 'PAD': 1}
id_to_word = {0: 'UNK', 1: 'PAD'}
id_for_sentence = []

id = 2
for sentence in tqdm(df_data['sentence_cut']):
    id_list = []
    for word in sentence:

        if word not in word_to_vector:
            id_list.append(word_to_id['UNK'])
        
        else:
            
            if word not in word_to_id:
                word_to_id[word] = id
                id_to_word[id] = word
                id += 1 

            id_list.append(word_to_id[word])

    id_for_sentence.append(id_list)

df_data['id_for_sentence'] = id_for_sentence

100%|██████████| 53360/53360 [00:00<00:00, 74469.78it/s]


In [8]:
df_data['id_for_sentence']

0        [2, 3, 4, 0, 5, 6, 7, 8, 9, 4, 10, 11, 6, 12, ...
1        [0, 23, 24, 25, 26, 27, 28, 0, 29, 30, 31, 32,...
2        [40, 41, 30, 42, 11, 43, 6, 44, 45, 46, 11, 6,...
3                  [53, 32, 54, 55, 56, 57, 0, 58, 59, 22]
4               [60, 34, 61, 62, 6, 0, 63, 64, 65, 66, 67]
                               ...                        
53355    [405, 447, 290, 0, 15918, 966, 81, 966, 13517,...
53356        [1379, 4833, 158, 84, 36245, 40657, 34, 2967]
53357    [44491, 848, 44492, 44493, 1264, 70, 11301, 75...
53358    [116, 107, 590, 34, 485, 3955, 6, 9846, 899, 2...
53359    [9619, 31951, 30867, 391, 6, 5303, 4172, 292, ...
Name: id_for_sentence, Length: 53360, dtype: object

## embedding matrix

构建词向量的矩阵，矩阵对应行的行数就是词的向量

In [9]:
embedding_mat = np.zeros(shape=(len(word_to_id), vector_dim))

for i in range(len(embedding_mat)):
    embedding_mat[i] = word_to_vector[id_to_word[i]]

## padding & truncated

让每个训练样本的序列长度一样，过长的截断，过短的补padding

In [10]:
max_length = 20

df_data['sentence_for_train'] = df_data['id_for_sentence'].apply(
    lambda x: x+[1]*(max_length-len(x)) if max_length > len(x) else x[:max_length])

# TextCNN Network

## backbone

In [129]:
import torch.nn as nn
import torch

class TextCNN(nn.Module):
    def __init__(self, embedding_tensor, seq_length, n_filter, filter_height_ls, n_class):
        super(TextCNN, self).__init__()
        self.embedding = nn.Embedding.from_pretrained(embedding_tensor)
        self.conv_ls = nn.ModuleList([nn.Conv2d(1, n_filter, (h, embedding_tensor.shape[1])) for h in filter_height_ls])
        self.maxpool_ls = nn.ModuleList([nn.MaxPool1d(seq_length-h+1) for h in filter_height_ls])
        self.relu = nn.ReLU()
        self.fc = nn.Linear(n_filter*len(filter_height_ls), n_class)
        self.dropout = nn.Dropout(p=0.8)
        self.softmax = nn.Softmax(dim=1)

    def conv_pool(self, x, conv, pool):
        x = conv(x).squeeze(3)
        x = self.relu(x)
        x = pool(x).squeeze(2)
        return x

    def forward(self, x):
        x = self.embedding(x).unsqueeze(1)
        x = torch.cat([self.conv_pool(x, conv, pool) for conv, pool in zip(self.conv_ls, self.maxpool_ls)], dim=1)
        # x = self.dropout(x)
        x = self.fc(x)
        out = self.softmax(x)
        return out

## focalloss

In [105]:
import torch.nn.functional as F

# 多分类
class MultiCEFocalLoss(nn.Module):
    def __init__(self, n_class, gamma, alpha=None):
        super(MultiCEFocalLoss, self).__init__()
        self.gamma = gamma
        self.alpha = torch.ones(n_class) if alpha is None else alpha
        self.n_class = n_class

    # y_pre softmax后的概率，y_ture 是 index
    def forward(self, y_pre, y_true):
        mask = F.one_hot(y_true, self.n_class)
        idx = y_true.view(-1,1)
        alpha = self.alpha[idx]
        probs = (mask * y_pre).sum(1).view(-1, 1)
        log_p = probs.log()
        loss = -alpha * (torch.pow((1 - probs), self.gamma)) * log_p
        return loss.sum()

## trainer

In [13]:
# !pip install pytorch_lightning

In [128]:
import torchmetrics
import pytorch_lightning as pl
import torch.nn as nn
import torch


class TrainModel(pl.LightningModule):
    def __init__(self, backbone):
        super(TrainModel, self).__init__()
        self.backbone = backbone
        self.loss = nn.CrossEntropyLoss()
        # self.loss = MultiCEFocalLoss(n_class, 5)
        self.lr = None
        self.acc = torchmetrics.Accuracy()

    def training_step(self, batch, batch_idx):
        x, y = batch
        output = self.backbone(x)
        loss = self.loss(output, y)
        score = self.acc(output, y)
        self.log('Training Loss', loss)
        self.log('Training Accuracy', score)
        return loss

    def validation_step(self, batch, batch_idx):
        x, y = batch
        output = self.backbone(x)
        score = self.acc(output, y)
        self.log('Validation Accuracy', score)
        return score
        
    def configure_optimizers(self):
        optimizer = torch.optim.Adam(self.parameters())
        return optimizer

    def forward(self, x):
        predict = self.backbone(x)
        predict = torch.argmax(predict, dim=1)
        return predict

## dataset

In [30]:
from torch.utils.data import TensorDataset, DataLoader
from sklearn.model_selection import train_test_split


x_tensor = torch.LongTensor([np.array(x) for x in df_data['sentence_for_train'].values])
y_tensor = torch.LongTensor(df_data['label_for_train'].values)

x_train, x_valid, y_train, y_valid = train_test_split(x_tensor, y_tensor, random_state=529)

train_loader = DataLoader(TensorDataset(x_train, y_train), batch_size=512, shuffle=True, num_workers=2)
valid_loader = DataLoader(TensorDataset(x_valid, y_valid), batch_size=512, num_workers=2)

## checkpoint

In [17]:
from pytorch_lightning.callbacks import ModelCheckpoint

checkpoint_callback = ModelCheckpoint(
    monitor='Validation Accuracy', 
    dirpath='/content/drive/MyDrive/Colab Notebooks Project/NLP/TouTiao_text/TextCNN/',
    filename='model-{epoch:02d}-{Validation Accuracy:.4f}',
    save_top_k=3, 
    mode='max')

/usr/local/lib/python3.7/dist-packages/pytorch_lightning/callbacks/model_checkpoint.py:360: UserWarning: Checkpoint directory /content/drive/MyDrive/Colab Notebooks Project/NLP/TouTiao_text/TextCNN/ exists and is not empty.
  rank_zero_warn(f"Checkpoint directory {dirpath} exists and is not empty.")


# Training

In [19]:
from pytorch_lightning import loggers as pl_loggers
%load_ext tensorboard
# %reload_ext tensorboard

The tensorboard extension is already loaded. To reload it, use:
  %reload_ext tensorboard


In [ ]:
%%time
# TextCNN setting
seq_length = max_length
n_filter = 5
filter_height_ls = [3,4,5]
n_class = df_data['label_for_train'].nunique()
embedding_tensor = torch.FloatTensor(embedding_mat)

# logger setting
log_name = '5-filter不带dropout'
version = '1000epoch'

network = TextCNN(embedding_tensor, seq_length, n_filter, filter_height_ls, n_class)
model = TrainModel(network)

# trainer = pl.Trainer(max_epochs=10, gpus=1, logger=pl_loggers.TensorBoardLogger('logs/'), callbacks=[checkpoint_callback])
trainer = pl.Trainer(max_epochs=1000, gpus=1, logger=pl_loggers.TensorBoardLogger('logs/', log_name, version))
# trainer = pl.Trainer(max_epochs=10,)

trainer.fit(model, train_loader, valid_loader)

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

  | Name     | Type             | Params
----------------------------------------------
0 | backbone | TextCNN          | 13.4 M
1 | loss     | CrossEntropyLoss | 0     
2 | acc      | Accuracy         | 0     
----------------------------------------------
18.3 K    Trainable params
13.3 M    Non-trainable params
13.4 M    Total params
53.467    Total estimated model params size (MB)


Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x7f662c633560>
Traceback (most recent call last):
  File "/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py", line 1328, in __del__
    self._shutdown_workers()
  File "/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py", line 1320, in _shutdown_workers
    if w.is_alive():
  File "/usr/lib/python3.7/multiprocessing/process.py", line 151, in is_alive
    assert self._parent_pid == os.getpid(), 'can only test a child process'
AssertionError: can only test a child process
Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x7f662c633560>
Traceback (most recent call last):
  File "/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py", line 1328, in __del__
    self._shutdown_workers()
  File "/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py", line 1320, in _shutdown_workers
    if w.is_alive():
  File "/usr/lib/pytho

Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x7f662c633560>
Traceback (most recent call last):
  File "/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py", line 1328, in __del__
    self._shutdown_workers()
  File "/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py", line 1320, in _shutdown_workers
    if w.is_alive():
  File "/usr/lib/python3.7/multiprocessing/process.py", line 151, in is_alive
    assert self._parent_pid == os.getpid(), 'can only test a child process'
AssertionError: can only test a child process
Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x7f662c633560>
Traceback (most recent call last):
  File "/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py", line 1328, in __del__
    self._shutdown_workers()
  File "/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py", line 1320, in _shutdown_workers
    if w.is_alive():
  File "/usr/lib/pytho

Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x7f662c633560>
Traceback (most recent call last):
  File "/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py", line 1328, in __del__
    self._shutdown_workers()
  File "/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py", line 1320, in _shutdown_workers
    if w.is_alive():
  File "/usr/lib/python3.7/multiprocessing/process.py", line 151, in is_alive
    assert self._parent_pid == os.getpid(), 'can only test a child process'
AssertionError: can only test a child process
Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x7f662c633560>
Traceback (most recent call last):
  File "/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py", line 1328, in __del__
    self._shutdown_workers()
  File "/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py", line 1320, in _shutdown_workers
    if w.is_alive():
  File "/usr/lib/pytho

Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x7f662c633560>
Traceback (most recent call last):
  File "/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py", line 1328, in __del__
    self._shutdown_workers()
  File "/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py", line 1320, in _shutdown_workers
    if w.is_alive():
  File "/usr/lib/python3.7/multiprocessing/process.py", line 151, in is_alive
    assert self._parent_pid == os.getpid(), 'can only test a child process'
AssertionError: can only test a child process
Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x7f662c633560>
Traceback (most recent call last):
Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x7f662c633560>
  File "/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py", line 1328, in __del__
    self._shutdown_workers()
Traceback (most recent call last):
  File "/usr/local/lib/python3

Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x7f662c633560>
Traceback (most recent call last):
  File "/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py", line 1328, in __del__
    self._shutdown_workers()
  File "/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py", line 1320, in _shutdown_workers
    if w.is_alive():
  File "/usr/lib/python3.7/multiprocessing/process.py", line 151, in is_alive
    assert self._parent_pid == os.getpid(), 'can only test a child process'
AssertionError: can only test a child process
Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x7f662c633560>
Traceback (most recent call last):
  File "/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py", line 1328, in __del__
    self._shutdown_workers()
Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x7f662c633560>
  File "/usr/local/lib/python3.7/dist-packages/torch/utils/data/d

In [2]:
%tensorboard --logdir logs

UsageError: Line magic function `%tensorboard` not found.
